# Počítačová algebra -- cvičení 5

## Úloha 1

In [31]:
"""Spočítá FFT, viz skripta
-- n: počet koeficientů
-- omega: příslušná n-tá odmocnina z 1
-- coeffs: koeficienty 
"""

def FFT(n,omega,coeffs):
    if n == 1:
        return coeffs
    n2 = n//2
    b = FFT(n2, omega*omega,[coeffs[2*i] for i in range(n2)]) #Alternativně coeffs[::2]
    c = FFT(n2, omega*omega,[coeffs[2*i+1] for i in range(n2)]) #coeffs[1::2]
    res = [0 for i in range(n)]
    om_pow = 1
    for i in range(n2):
        temp = om_pow*c[i]
        res[i] = b[i]+temp
        res[n2+i] = b[i]-temp
        om_pow *= omega
    return res
        
#Inverzní FFT
def IFFT(n,omega,coeffs):
    inv = omega^(-1)
    return [(omega.parent()(n))^(-1)*elem for elem in FFT(n,inv,coeffs)] 
#omega.parent() najde okruh ze kterého je omega, aby v něm mohla invertovat n

In [66]:
"""Funkce pro násobení dvou celočíselných polynomů za použítí komplexních odmocnin z 1
-- f,g: libovolné polynomy
-- prec: počet bitů s jejichž přesností se počítá v komplexních číslech
"""
def mul_complex(f,g, prec = 64):
    C = ComplexField(prec)
    n = f.degree()+g.degree()+1
    n = 1 << n.nbits() #dosadí do n nejbližší větší mocninu 2 než (stupeň f + stupeň g)
    
    f_coeffs = f.coefficients(sparse=False)+[0] * (n - f.degree()-1) #doplní nulami koeficienty f a g do počtu n 
    g_coeffs = g.coefficients(sparse=False)+[0] * (n - g.degree()-1) #k získání koef. lze použít i např. f.list()
    omega = C(e^(2*pi*I/n)) #n-tá odmocnina z 1
    F = FFT(n,omega,f_coeffs)
    G = FFT(n,omega,g_coeffs)
    RES = [F[i]*G[i] for i in range(n)]
    res = IFFT(n,omega,RES)
    #print(res[::-1])
    res = [item.real().round() for item in res] #vezme z komplexního čísla reálnou část a zaokrouhlí ji na nejbližší celé číslo
    return f.parent(res) #převede koeficienty zpátky do polynomu z původního oboru (ten je = f.parent())

In [263]:
P.<t> = ZZ[]
f = P.random_element(degree=10)
g = P.random_element(degree=10)
a = mul_complex(f,g, prec=10)
b = f*g
print(a)
print(b)
print(a==b)

4*t^31 + t^30 + 3*t^29 + t^28 + t^26 + 2*t^25 + 2*t^24 + t^23 + t^22 - t^21 + 3*t^20 + 14*t^18 - 4*t^17 - 12*t^16 + 32*t^15 + 11*t^14 - 586*t^13 - 573*t^12 - 4040*t^11 + 1704*t^10 + 606*t^9 - 578*t^8 - 598*t^7 + 571*t^6 + 584*t^5 - 6*t^4 + 1728*t^3 + 10*t^2 - 13*t - 2
2*t^20 + 2*t^19 + 12*t^18 - 5*t^17 - 11*t^16 + 31*t^15 + 10*t^14 - 589*t^13 - 574*t^12 - 4031*t^11 + 1723*t^10 + 611*t^9 - 586*t^8 - 593*t^7 + 574*t^6 + 583*t^5 - 7*t^4 + 1726*t^3 + 3*t^2 - 15*t
False


## Úloha 2

In [93]:
R.<s> = QQ[]
f = 1/3*s^3+1/5+1/6*s
print(f.denominator()) # takto se dá získat NSN všech jmenovatelů koeficientů polynomu

30


In [1]:
# Vynásobí dva racionální polynomy za pomocí komplexní odmocniny z 1 a FFT
def fast_mul_rat(f,g, prec=64):
    a = f.denominator()
    b = g.denominator()
    ff = (a*f).change_ring(ZZ)
    gg = (b*g).change_ring(ZZ)
    res = mul_complex(ff,gg,prec).change_ring(QQ)
    return res/(a*b)


In [102]:
R.<s> = QQ[]
f = 1/3*s^3+1/6*s+1/5
g =2*s^2+1/4
print(fast_mul_rat(f,g))

2/3*s^5 + 5/12*s^3 + 2/5*s^2 + 1/24*s + 1/20


## Úloha 3

In [114]:
PP.<y> =  QQ[[]] #syntax je podobná jako u okruhu polynomů, pouze se použije dvojitá závorka [[]]

In [115]:
t = PP.random_element(prec=6) #vezme náhodný prvek, prec specifikuje kolik členů nás zajímá a co už se schová do klasické O notace
print(t)
print(t.coefficients()) #podobně t.list(), etc.
print(1/t) #udělá inverz
print(t.O(3)) #takto můžeme upravit přesnost na méně členů než máme

-1/2*y - 1/6*y^2 + 2/5*y^3 + 1/19*y^4 - y^5 + O(y^6)
[-1/2, -1/6, 2/5, 1/19, -1]
-2*y^-1 + 2/3 - 82/45*y + 2386/2565*y^2 + 88582/38475*y^3 + O(y^4)
-1/2*y - 1/6*y^2 + O(y^3)


## Úloha 4

In [125]:
PP.<y> =  QQ[[]]

print(exp(y).O(10)) #V sagi funguje pro mocninné řady několik funkcí jako exp, sin, cos.. které můžeme aplikovat na již existující řady
print(cos(y^2+y).O(10))

#Podobně funguje manipulace se řadami tímto stylem
print("\n--------- Rozvoj 1/(1-y) ---------")
print(1/(1-y)) #všimněte si jak to souvisí se součtem geometrické posloupnosti

1 + y + 1/2*y^2 + 1/6*y^3 + 1/24*y^4 + 1/120*y^5 + 1/720*y^6 + 1/5040*y^7 + 1/40320*y^8 + 1/362880*y^9 + O(y^10)
1 - 1/2*y^2 - y^3 - 11/24*y^4 + 1/6*y^5 + 179/720*y^6 + 19/120*y^7 + 841/40320*y^8 - 139/5040*y^9 + O(y^10)

--------- Rozvoj 1/(1-y) ---------
1 + y + y^2 + y^3 + y^4 + y^5 + y^6 + y^7 + y^8 + y^9 + y^10 + y^11 + y^12 + y^13 + y^14 + y^15 + y^16 + y^17 + y^18 + y^19 + O(y^20)


## Úloha 5

Na cviku se nestihlo, ponecháno v rámci domácího úkolu č. 3

## Úloha 6

Možností je spousta, některé různě efektivní od dalších.. Jedna z nich je procházet všechna čísla tvaru a*2^k+1 a zkoušet, jestli jsou prvočísla.

Obecně je fajn si ta prvočísla předem stanovit napevno, pokud víme s jak velkými hodnotami pracujeme než je někdy v průběhu výpočtu opakovaně hledat..

In [147]:
# Najde prvočíslo p>n, že 2^k | p-1.
def find_suitable_prime(k,n):
    p = 1 << (n.nbits() - k) #najde nějaké číslo dost velké, aby p*2^k > n jako začátek
    pow2 = 1 << k #t = 2^k
    p=p*pow2+1 #tvar a*2^k+1
    
    while True:
        p+=pow2
        if p.is_prime():
            break
    return p


In [156]:
find_suitable_prime(3000,2^100)

## Úloha 7

In [235]:
#Modulárně za pomocí FFT vynásobí dva celočíselné polynomy
def modular_fast_mul(f,g):
    if f == 0 or g == 0:
        return f.parent(0)
    k = (f.degree()+g.degree()+1).nbits() #aby 2^k>f.degree()+g.degree()
    r = max(abs(max(f)),abs(min(f)))
    s = max(abs(max(g)),abs(min(g)))
    n = 2*(max(f.degree(),g.degree())+1)*r*s
    p = find_suitable_prime(k,n)
    
    pow2 = 2^k 
    F = Zmod(p)
    S = F['x']
    fp = S(f) #polynomials in Zmod(p)[]
    gp = S(g)
    omega = F.multiplicative_generator() #finds pow2-th root of unity in Zmod(p)
    omega = omega^(omega.multiplicative_order()>>k)
    
    f_coeffs = fp.list()+[F(0)] * (pow2 - fp.degree()-1) #doplní nulami koeficienty f a g do počtu k
    g_coeffs = gp.list()+[F(0)] * (pow2 - gp.degree()-1)
    F = FFT(pow2,omega,f_coeffs)
    G = FFT(pow2,omega,g_coeffs)
    RES = [F[i]*G[i] for i in range(pow2)]
    res = IFFT(pow2,omega,RES)
    for i in range(len(res)):
        res[i] = ZZ(res[i])
        if res[i]> p//2:
            res[i] -= p #preved cleny zpatky do intervalu [-p//2,p//2]
    return f.parent(res)
    

In [250]:
P.<r> = ZZ[]
f = P.random_element(degree=5)
g = P.random_element(degree=5)
a = modular_fast_mul(f,g)
b = f*g
print(a)
print(b)
print(a==b)

r^10 + 4*r^9 - 3*r^7 - 114*r^6 - 466*r^5 - 117*r^4 - r^3 + r^2 - 117*r
r^10 + 4*r^9 - 3*r^7 - 114*r^6 - 466*r^5 - 117*r^4 - r^3 + r^2 - 117*r
True


In [257]:
#Příklad velmi jednoduchého srovnání na 1 případě, v domácím úkolu čekám detailnější viz např. první cvičení (srovnávání pro různé stupně, atd.)
f = P.random_element(degree=500)
g = P.random_element(degree=500)

print(timeit("modular_fast_mul(f,g)"))
print(timeit("mul_complex(f,g)"))

5 loops, best of 3: 78.6 ms per loop
5 loops, best of 3: 135 ms per loop
